## Enabling Altair for the notebook

Altair is installed by following this guide
https://altair-viz.github.io/getting_started/installation.html

In [ ]:
import altair as alt
#alt.renderers.enable('notebook')

In [ ]:
import pandas as pd

## Brain Body Visualization

In [ ]:
brain_body = pd.read_csv("https://raw.githubusercontent.com/rezpe/datos_viz/master/brain.csv")

In [ ]:
brain_body.head()

Index  Brain Weight  Body Weight
0      1         3.385         44.5
1      2         0.480         15.5
2      3         1.350          8.1
3      4       465.000        423.0
4      5        36.330        119.5

In [ ]:
hist_brain = alt.Chart(brain_body).mark_bar().encode(
    alt.X("Brain Weight:Q", bin=True),
    y='count()',
)
hist_brain

alt.Chart(...)

In [ ]:
hist_brain = alt.Chart(brain_body).mark_bar().encode(
    alt.X("Brain Weight:Q", bin=alt.Bin(maxbins=100)),
    y='count()',
)
hist_brain

alt.Chart(...)

In [ ]:
hist_body = alt.Chart(brain_body).mark_bar().encode(
    alt.X("Body Weight:Q", bin=alt.Bin(maxbins=100)),
    y='count()',
)
hist_body

alt.Chart(...)

In [ ]:
scatter_body_brain = alt.Chart(brain_body).mark_circle().encode(
x="Body Weight:Q",
y="Brain Weight:Q")
scatter_body_brain

alt.Chart(...)

In [ ]:
(hist_body|hist_brain)&scatter_body_brain

alt.VConcatChart(...)

## Search Trends

In [ ]:
trends = pd.read_csv("https://raw.githubusercontent.com/rezpe/datos_viz/master/google_trends.csv")

In [ ]:
trends.head()

date search_term  value
0  2004-01   SPSS data      6
1  2004-02   SPSS data      8
2  2004-03   SPSS data      7
3  2004-04   SPSS data      7
4  2004-05   SPSS data      6

In [ ]:
evolution = alt.Chart(trends).mark_line().encode(
x="date:T",
    y="mean(value)",
    color="search_term:N"
)
evolution

alt.Chart(...)

In [ ]:
comparison = alt.Chart(trends).mark_bar().encode(
    x="search_term:N",
    y="mean(value)",
    color="search_term:N"
)
comparison

alt.Chart(...)

In [ ]:
evolution|comparison

alt.HConcatChart(...)

In [ ]:
select_search_term = alt.selection_single(encodings=["x"])

evolution = alt.Chart(trends).mark_line().encode(
x="date:T",
    y="mean(value)",
    color="search_term:N"
).properties(

).transform_filter(
    select_search_term.ref()
)

comparison = alt.Chart(trends).mark_bar().encode(
    x="search_term:N",
    y="mean(value)",
    color="search_term:N"
).properties(
selection=select_search_term
)

total_chart = comparison|evolution
total_chart

alt.HConcatChart(...)

In [ ]:
# Interactivity to select

In [ ]:
select_date = alt.selection(type="interval",encodings=["x"])

evolution = alt.Chart(trends).mark_line().encode(
    x="yearmonth(date)",
    y="mean(value)",
    color="search_term:N"
).properties(
    selection=select_date
)

comparison = alt.Chart(trends).mark_bar().encode(
    x="search_term:N",
    y="mean(value)",
    color="search_term:N",
).transform_filter(
    select_date.ref()
)

total_chart = comparison|evolution
total_chart

alt.HConcatChart(...)

In [ ]:
# Interactivity to Zoom

In [ ]:
select_date = alt.selection(type="interval",encodings=["x"])

evolution = alt.Chart(trends).mark_line().encode(
    x="date:T",
    y="mean(value)",
    color="search_term:N"
)

comparison = evolution.transform_filter(
    select_date.ref()
)

total_chart = comparison|evolution.properties(
    selection=select_date
)
total_chart

alt.HConcatChart(...)

# Weather Temperature

In [ ]:
df = pd.read_csv("https://github.com/rezpe/datos_viz/raw/master/worldTemperatures.csv",header=None)
df.columns=["0", "1", "2", "date", "4", 'temp', "6", "7", "8", "9", "10", 'latitude', 'longitude',
        'country','city',]
df["date"]=pd.to_datetime(df["date"],format="%Y%m%d")

In [ ]:
df.head()

0       1            2  ... longitude      country       city
0  0   51957  IVM00065594  ... -6.660817  Ivory Coast  San Pedro
1  1  141546  IVM00065594  ... -6.660817  Ivory Coast  San Pedro
2  2  231680  IVM00065594  ... -6.660817  Ivory Coast  San Pedro
3  3  323605  IVM00065594  ... -6.660817  Ivory Coast  San Pedro
4  4  416249  IVM00065594  ... -6.660817  Ivory Coast  San Pedro

[5 rows x 15 columns]

In [ ]:
## Overide the limit
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [ ]:
temp = df.groupby(["country","date"]).mean().reset_index()
temp["temp"]=temp["temp"].astype(float)

bar = alt.Chart(temp[["country","temp"]]).mark_bar().encode(
    x='country:N',
    y='mean(temp)',
    tooltip="country:N"
).properties(
    width=2000,
    height=200
)
bar

alt.Chart(...)

In [ ]:
temp = df.groupby(["country","date"]).mean().reset_index()

pts = alt.selection_single(encodings=["x"])

bar = alt.Chart(temp).mark_bar().encode(
    x=alt.X('country:N'),
    y='mean(temp)',
    tooltip="country:N"
).properties(
    width=2000,
    height=200,
    selection=pts
)

line = alt.Chart(temp).mark_line().encode(
    x='date:T',
    y='mean(temp)',
).transform_filter(
    pts.ref()
).properties(
    width=800,
    height=200,
    
)

alt.vconcat(line, bar, data=temp)

alt.VConcatChart(...)

In [ ]:
# Maps Reference 
# https://stackoverflow.com/questions/55923300/how-can-i-make-a-map-using-geojson-data-in-altair

In [ ]:
states = alt.topo_feature("https://unpkg.com/world-atlas@1/world/110m.json", feature='countries')

# US states background
background = alt.Chart(states).mark_geoshape(
    fill='lightgray',
    stroke='white'
).properties(
    width=300,
    height=300
)

temp = df.groupby(["country"]).mean().reset_index()
points = alt.Chart(temp).mark_circle().encode(
    longitude='longitude:Q',
    latitude='latitude:Q',
    size=alt.value(10),
    color=alt.Color('temp:Q',scale=alt.Scale(range=['blue',"orange",'red']))
).properties(
    width=300,
    height=300
)

mapchart = background +points
mapchart

alt.LayerChart(...)

In [ ]:
# Themes

In [ ]:
config = {'arc': {'fill': '#30a2da'},
 'area': {'fill': 'black'},
 'axisBand': {'grid': False},
 'axisBottom': {'domain': False,
  'domainColor': '#999',
  'domainWidth': 3,
  'grid': False,
  'gridColor': '#cbcbcb',
  'gridWidth': 1,
  'labelColor': '#999',
  'labelFontSize': 14,
  'labelPadding': 4,
  'tickColor': 'white',
  'tickSize': 10,
  'titleFontSize': 14,
  'titlePadding': 10},
 'axisLeft': {'domainColor': 'white',
  'domainWidth': 1,
  'grid': False,
  'gridColor': 'white',
  'gridWidth': 1,
  'labelColor': 'white',
  'labelFontSize': 10,
  'labelPadding': 4,
  'tickColor': 'white',
  'tickSize': 10,
  'ticks': True,
  'titleFontSize': 14,
  'titlePadding': 10},
 'axisRight': {'domainColor': '#333',
  'domainWidth': 1,
  'grid': True,
  'gridColor': '#cbcbcb',
  'gridWidth': 1,
  'labelColor': 'white',
  'labelFontSize': 10,
  'labelPadding': 4,
  'tickColor': 'white',
  'tickSize': 10,
  'ticks': True,
  'titleFontSize': 14,
  'titlePadding': 10},
 'axisTop': {'domain': False,
  'domainColor': '#333',
  'domainWidth': 3,
  'grid': False,
  'gridColor': '#cbcbcb',
  'gridWidth': 1,
  'labelColor': '#999',
  'labelFontSize': 10,
  'labelPadding': 4,
  'tickColor': '#cbcbcb',
  'tickSize': 10,
  'titleFontSize': 14,
  'titlePadding': 10},
 'background': 'white',
 'group': {'fill': 'black',"stroke":"white"},
 'legend': {'labelColor': '#333',
  'labelFontSize': 14,
  'padding': 1,
  'symbolSize': 30,
  'symbolType': 'square',
  'titleColor': '#333',
  'titleFontSize': 14,
  'titlePadding': 10},
 'line': {'stroke': '#30a2da', 'strokeWidth': 2},
 'path': {'stroke': '#30a2da', 'strokeWidth': 0.5},
 'rect': {'fill': '#30a2da'},
 'range': {'category': ['#30a2da',
   '#fc4f30',
   '#e5ae38',
   '#6d904f',
   '#8b8b8b',
   '#b96db8',
   '#ff9e27',
   '#56cc60',
   '#52d2ca',
   '#52689e',
   '#545454',
   '#9fe4f8'],
  'diverging': ['#cc0020',
   '#e77866',
   '#f6e7e1',
   '#d6e8ed',
   '#91bfd9',
   '#1d78b5'],
  'heatmap': ['#d6e8ed', '#cee0e5', '#91bfd9', '#549cc6', '#1d78b5']},
 'symbol': {'filled': True, 'shape': 'circle'},
 'shape': {'stroke': 'white'},
 'style': {'bar': {'binSpacing': 2, 'fill': '#30a2da', 'stroke': None}},
 'title': {'anchor': 'start', 'fontSize': 24, 'fontWeight': 600, 'offset': 20},
         "view": {
     "stroke": "transparent"
  }}

In [ ]:
def my_theme():
    return {'config': config }

alt.themes.register('my_theme', my_theme)

alt.themes.enable('my_theme')

ThemeRegistry.enable('my_theme')

In [ ]:
hist_brain = alt.Chart(brain_body).mark_bar().encode(
    alt.X("Brain Weight:Q", bin=alt.Bin(maxbins=100)),
    y='count()',
)
hist_brain

alt.Chart(...)

In [ ]:
evolution = alt.Chart(trends).mark_line().encode(
    x=alt.X("year(date):T",title="Year"),
    y=alt.Y("mean(value)",title="Searches"),
    color="search_term:N",
    tooltip="mean(value)"
).properties(
width=700)

evolution

alt.Chart(...)

In [ ]:
evolution = alt.Chart(trends[(trends["date"].str.contains("2017"))|(trends["date"].str.contains("2007"))])\
.mark_bar().encode(
    x="year(date):T",
    y="mean(value)",
    color="search_term:N",
    tooltip="mean(value)"
).properties(
width=600)
evolution

alt.Chart(...)